### Ejercicios API Foursquare

In [1]:
import numpy as np
import pandas as pd

import requests
from pprint import pprint

import folium

In [26]:
folium.__version__

'0.14.0'

### Credenciales

In [2]:
# Credenciales

with open ('../11.APIS/src/credenciales.txt', 'r') as file:  #las credenciales no deberian ponerse en un notebook ni en un repositorio
    secrets = file.read()                               #creamos un archivo txt con nuestras credenciales poner en git ignore para que no suba al repo el archivo de credenciales
credentials = (
    {
    secreto.split(' = ')[0]:secreto.split(' = ')[1] 
    for secreto in secrets.split('\n')
    }
)


### Ejercicio 1:

- Haz una consulta usando el API de **`Foursquare Places`** y genera un **`DataFrame`** con esta información. Este **`DataFrame`** debe tener la información de latitud y longitud.
- En un mapa de **`folium`** muestra la información del **`DataFrame`**.

CONSULTA:

In [3]:
# Base del Endpoint
search_url = "https://api.foursquare.com/v3/places/search"

url_params = {"queary"     : "Universities",
              "ll"         : "46.0,2.0",
              "open_now"   : None,
              "limit"      : 50,
              "radius"     : 100_000,
              "category"   : None}

headers = {"accept"         : "application/json",
           "Authorization"  : credentials['clave_api']}

# Como ahora usamos una variable para los parámetros, debemos agregarlos con el parámetro "params"
response = requests.get(url = search_url, params = url_params, headers = headers)
print(f"endpoint: {response.url}")

print(f"response: {response.status_code}")

print(response.json())
pprint(response.json())

endpoint: https://api.foursquare.com/v3/places/search?queary=Universities&ll=46.0%2C2.0&limit=50&radius=100000
response: 200
{'results': [{'fsq_id': '4f7f42e27b0cf18ae1af0b85', 'categories': [{'id': 13334, 'name': 'Sandwich Spot', 'short_name': 'Sandwich Spot', 'plural_name': 'Sandwich Spots', 'icon': {'prefix': 'https://ss3.4sqi.net/img/categories_v2/food/deli_', 'suffix': '.png'}}], 'chains': [], 'closed_bucket': 'LikelyOpen', 'distance': 26185, 'geocodes': {'main': {'latitude': 46.19769, 'longitude': 2.185067}, 'roof': {'latitude': 46.19769, 'longitude': 2.185067}}, 'link': '/v3/places/4f7f42e27b0cf18ae1af0b85', 'location': {'address': 'Aire Bi-directionelle', 'admin_region': 'Limousin', 'country': 'FR', 'formatted_address': 'Aire Bi-directionelle, 23140 Parsac', 'locality': 'Parsac', 'postcode': '23140', 'region': 'Nouvelle-Aquitaine'}, 'name': 'Brioche Dorée', 'related_places': {}, 'timezone': 'Europe/Paris'}, {'fsq_id': '4ec7bf0c0e6158bafed5178b', 'categories': [{'id': 19014, 'na

In [4]:
data = response.json()
df = []
for d in data["results"]:

    fsq_id = d["fsq_id"]
    try:
        category = d["categories"][0]["name"]
    except:
        category = np.nan
    latitude = d["geocodes"]["main"]["latitude"]
    longitude = d["geocodes"]["main"]["longitude"]
    location = d["location"]["formatted_address"]
    region = d["location"]["region"]
    name = d["name"]

    df.append([name, category, location, latitude, longitude, region, fsq_id])

df_unifrance = pd.DataFrame(data = df, columns = ["Name", "Category", "Location", "Latitude", "Longitude", "Region", "fsq_id"])


In [11]:
df_unifrance.head()

Name           Category  \
0          Brioche Dorée      Sandwich Spot   
1   Château de la Cazine              Hotel   
2  Les Tables du Bistrot  French Restaurant   
3          Chez Alphonse          Brasserie   
4    La Fabrique du Café               Café   

                               Location   Latitude  Longitude  \
0   Aire Bi-directionelle, 23140 Parsac  46.197690   2.185067   
1    2012 Domaine de la Fot, 23300 Noth  46.240698   1.558729   
2  32 rue du Grand-Theil, 87280 Limoges  45.871235   1.277929   
3    5 place de la Motte, 87000 Limoges  45.829185   1.256600   
4        12 place d'Aine, 87000 Limoges  45.829782   1.254721   

               Region                    fsq_id  
0  Nouvelle-Aquitaine  4f7f42e27b0cf18ae1af0b85  
1  Nouvelle-Aquitaine  4ec7bf0c0e6158bafed5178b  
2  Nouvelle-Aquitaine  4bff9f40ca1920a19f02ed81  
3  Nouvelle-Aquitaine  4bab4a0ef964a5201a9e3ae3  
4  Nouvelle-Aquitaine  50a7b94de4b0d7e300662dd3

In [30]:
latitude = 46.5647432
longitude = -0.7381561

In [35]:
# Volvemos a inicializar el mapa
sf_map = folium.Map(location = [latitude, longitude], zoom_start = 6)

# Inicializamos un FeatureGroup() para los incidentes en el DataFrame
incidents = folium.map.FeatureGroup()

# Recorre los 100 crímenes y agrega a cada uno al FeatureGroup() de incidentes
# La columna Y y X son las coordenadas, latitud y longitud respectivamente
# La columna "Category" es el tipo de incidente.

for lat, lng, label, catego, loc in zip(df_unifrance["Latitude"], df_unifrance["Longitude"], df_unifrance["Name"], df_unifrance["Category"], df_unifrance["Location"]):
    
    incidents.add_child(folium.Marker(location = [lat, lng],
                                      popup    = [label, catego, loc]))
    
# Agrega incidentes al map
sf_map.add_child(incidents)

sf_map

In [24]:
world_geo = "../Actividades/geojson/arrondissements-avec-outre-mer.geojson" # Archivo GeoJSON
# Crea un mapa francia
world_map = folium.Map(location = [latitude, longitude], zoom_start = 5)
folium.Choropleth(geo_data = world_geo,
                  data     = df_unifrance,
                  columns  = ["Name", "Longitude"],
                  key_on   = "properties.nom",
                  fill_color   = "Blues_r", 
                  fill_opacity = 0.7, 
                  line_opacity = 0.2,
                  legend_name  = "Region").add_to(world_map)

world_map

### Ejercicio 2:
- Haz otra consulta usando el API de **`Foursquare Places`** y genera un **`DataFrame`** con esta información, ésta vez que sea una consulta mucho más general y que sea por provincia de España o país Europeo. En cada caso la búsqueda debe estar centrada en la capital de cada provincia o país.
- Muestra la información usando un mapa **`Choropleth`**.

Recuerda buscar un archivo **`GeoJSON`** que se adapte a la información que quieres mostrar.